# Fórum do SIGAA - PLN

###### Holanda, Jong, Lourenço, Oliveira

## Requirements

Lets first install all necessary stuff.

In [1]:
%pip install --upgrade nbformat
%pip install plotly
%pip install spacy
%pip install nltk
%pip install matplotlib
%pip install ipython
%pip install ipywidgets
%pip install regex
%pip install bertopic
%pip install langchain langchain_openai

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated pa

In [2]:
!jupyter nbextension enable --py widgetsnbextension

usage: jupyter [-h] [--version] [--config-dir] [--data-dir] [--runtime-dir]
               [--paths] [--json] [--debug]
               [subcommand]

Jupyter: Interactive Computing

positional arguments:
  subcommand     the subcommand to launch

options:
  -h, --help     show this help message and exit
  --version      show the versions of core jupyter packages and exit
  --config-dir   show Jupyter config dir
  --data-dir     show Jupyter data dir
  --runtime-dir  show Jupyter runtime dir
  --paths        show all Jupyter paths. Add --json for machine-readable
                 format.
  --json         output paths as machine-readable json
  --debug        output debug information about paths

Available subcommands: dejavu events execute kernel kernelspec lab
labextension labhub migrate nbconvert notebook run server troubleshoot trust

Jupyter command `jupyter-nbextension` not found.


In [3]:
!python3 -m spacy download pt_core_news_sm

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 8.0 MB/s eta 0:00:0000:0100:01
✔ Download and installation successful
You can now load the package via spacy.load('pt_core_news_sm')


### Data Collect

Our aim was to obtain messages from "Fórum do SIGAA". Because SIGAA does not provide an API to collect that data, it was needed apply web scrapping techniques. It is important to notice that the messages are limited to the course BTI and do not represent all messages in the web plataform.

### Exploration

It is known (so far) that the forum consists of topics that are created by students and professors related to BTI. The topic is represented by title, author, how many messages (do not include the first message from author) and last message sent datetime. Besides, topic answers are represented by sent datetime, author with registration code (matrícula), content.

From date of collect, it was noticed that there was 3070 registered topics in the forum. They are presented by pages of 30 topics, so there are in total 103 pages. But that does not express the depth of messages registered. In total, there was 11920 messages in almost 11 years (2013 to 2024).

Let's have a look at our dataset:

In [2]:
import pandas as pd

df = pd.read_json('dataset/forum.json')

df.head()

titulo        data      hora  \
0  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  12:14:06   
1  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  13:47:55   
2  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  14:09:01   
3  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  15:15:12   
4  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  15:26:24   

                                     nome  \
0         MARINA MEDEIROS DE ARAÚJO LEITE   
1               RAMON OLIVEIRA DE ALMEIDA   
2  ANDRIEL VINICIUS DE MEDEIROS FERNANDES   
3          GABRIEL CARVALHO PEREIRA SILVA   
4           HIRANILSON ANDRADE DOS SANTOS   

                                            conteudo  
0  Nós do PET CC queremos saber qual é o interess...  
1  Se der pra participar deste e do outro(linux +...  
2                                  Tenho interesse\n  
3                                  tenho interesse\n  
4            tenho interesse se for no formato ead\n

An initial glance at the dataset shows us two areas of interest, the titles and the contents. The texts so far also seem surprisingly clean, but let's check further.

We can start by isolating the collumns of interest.

We could leave titles attached to their respective content, but notice how titles repeat themselves in that format. Any analysis or model built on that would be heavily biased towards the words in the titles, which would not be necessarily representative of the forum as a whole.

In [3]:
df_titles = df['titulo']
df_content = df['conteudo']

print(df_titles.shape, df_content.shape)

(11922,) (11922,)


We can then easily get rid of repeated values in the titles with the pandas df.drop_duplicates method

In [4]:
df_titles.drop_duplicates(inplace = True)

df_titles.shape

(2711,)

Analysing content and titles separately may be worthwhile, but it may also be interesting to see what we can get using both at once.

In [5]:
df_text = pd.concat([df_titles, df_content], axis=0)

df_text.shape

(14633,)

Now that we have our datasets, let's check them again. First, messages contents:

In [6]:
for content in df_content.sample(10, random_state=200):
    print(content)

Tem alguma previsão para o início das aulas?

Me interesso em DIM0346 - GERENCIAMENTO E SEGURANCA EM REDES DE COMPUTADORES.
Turnos: vespertino ou noturno.

up

kkkkkkkkkkkkkkkkkkkkkkkkkk desculpe Anrafell

IMD0902 é "INGLES TECNICO I" ou "Introdução à Internet das Coisas"?

Boa noite galera de TI!

NOSSOS CANECOS FINALMENTE PRONTINHOS PARA DISTRIBUIÇÃO

E sabe qual a melhor parte?

Você que comprou o Projeto ReX (festa de integração) vai ter em primeira mão!!

A primeira distribuição dos canecos será durante o PROJETO REX

Para aqueles que não compraram o caneco, temos uma boa notícia, ESTAREMOS VENDENDO NO PROJETO REX!!

CANECO + TIRANTE APENAS R$ 40,00

OBS: Aqueles que não pegarem durante o integra, ainda divulgaremos próxima semana como será o esquema para todo mundo pegar o caneco

Confere o vídeo no insta no link abaixo para ver o resultado iradooooo dos nossos canecos

https://www.instagram.com/reel/Cq9GBVjrg4Y/?igshid=YmMyMTA2M2Y=

Tenho interesse em participar, quais os pré re

Second, titles:

In [9]:
for title in df_titles.sample(10, random_state=200):
    print(title, '\n')

[Sugestão] Salas de estudos divididas 

VTEX no IMD - UFRN | 29/08 

Novas turmas criadas HOJE 

Processos de aproveitamento de estudos 

GRUPO PARA OS FORMANDOS 

Solicitação de Componente Curricular 

PROJETO DE EXTENSÃO - Oficina de Expressão Oral em Língua Inglesa 

Oportunidade de Bolsa 

Ferramentas para a disciplina IMD1001 - MATEMÁTICA ELEMENTAR 

Novo Coordenador e Sala da Coordenação 



In [10]:
for txt in df_text.sample(10, random_state=300):
    print(txt, '\n')

Nova Disciplina 

Fui assaltado também na minha primeira semana no IMD, isso em 2020, enquanto aguardava na parada próximo às residencias universitarias. Muito perigoso.
 

Existe algum meio no SiGAA para conferir se o vínculo foi confirmado?
 

Jefferson,

pode ser que para alguns alunos aconteça algum problema. Peço que tente novamente em outro PC e veja se a unidade está montada.

Caso tenha algum problema, procure o pessoal da TI na sala B115.
 

Obrigado.
 

Obrigado Rubem.
 

Pessoal, eu fiz prova na sala A306 e esqueci minha garrafa d'água na sala. É uma garrafa de alumínio prateada... Se alguém encontrar por favor deixem na secretaria. Agradeço desde ja
 

Cade as disciplinas na sexta 6N1234 ??? Quem quer pagar no mínimo 5 matérias não consegue....
 

@jessielylvr
 

Cine Empreender com a SoftUrbano 



## Cleaning

As far as texts with no standard format (like the ones in an online forum) go, these are surprisingly clean so far. Most of what could be considered thrash for our purposes are links, emails and citations. Removing special characters later on would result in a lot of gibberish from these cases, but they are also not particularly easy to isolate. Selecting the most frequent words for our vocabulary might be enough to get rid of these extra data. But let's do some tests.

In [8]:
import re

def remove_emails_com(text):
    return re.sub(r'[^\s]+.com', '', text).strip()

def remove_emails_br(text):
    return re.sub(r'[^\s]+.br', '', text).strip()

def remove_links(text):
    return re.sub(r'http[^\s]+', '', text).strip()

def remove_citations(text):
    return re.sub(r'@[^\s]+', '', text).strip()

def remove_numbers(text):
    return re.sub(r'\d+', '', text).strip()

def remove_special_characters(text):
    return re.sub(r'[^\w\s.!?]', '', text).strip()

def remove_empty_lines(text):
    return "\n".join([line for line in text.split('\n') if line.strip() != ''])

test_str = "mande para o email sample_email@ufrn.edu.br ou sample_email@gmail.com, ou se   inscreva no site https://url.com.br/inscricao - @user"

result = remove_links(test_str)
result = remove_emails_br(result)
result = remove_emails_com(result)
result = remove_citations(result)
result = remove_numbers(result)
result = remove_special_characters(result)
result = remove_empty_lines(result)


print(result)

mande para o email  ou  ou se   inscreva no site


These seems to work well enough. Other than that, we could check for spelling errors. However, the texts seem clean enough and spelling erros can be eliminated by frequency, so for now let's skip that step. Let's just add a function to get rid of random formatting like lines and tabs. We can also get rid of repeated symbols and possible punctuation errors.

In [9]:
def remove_repeated_symbols(text):
    return re.sub(r'(\W)\1+', r'\1', text).strip()

def remove_excessive_spaces(text):
    return re.sub(r'\s+', ' ', text).strip()

def fix_isolated_commas(text):
    # Replace punctuation with a blank character before
    text = re.sub(r' ([.,:;!?])', r'\1', text)
    return text.strip()

Now we just need to build our pipeline.

In [10]:
from sklearn.pipeline import Pipeline # Pipeline applies a list of transforms. You can also add an estimator at the end, so it will be completely encapsulated.
from sklearn.preprocessing import FunctionTransformer # FunctionTransformer allows to apply an arbitrary function to the data, so we can use it in the pipeline


pipeline_clean_text = Pipeline([
    ('remove_links', FunctionTransformer(remove_links)),
    ('remove_emails_br', FunctionTransformer(remove_emails_br)),
    ('remove_emails_com', FunctionTransformer(remove_emails_com)),
    ('remove_citations', FunctionTransformer(remove_citations)),
    ('remove_excessive_spaces', FunctionTransformer(remove_excessive_spaces)),
    ('remove_repeated_symbols', FunctionTransformer(remove_repeated_symbols)),
    ('fix_isolated_commas', FunctionTransformer(fix_isolated_commas)),
    ('remove_numbers', FunctionTransformer(remove_numbers)),
    ('remove_special_characters', FunctionTransformer(remove_special_characters)),
    ('remove_empty_lines', FunctionTransformer(remove_empty_lines)),

])

# We can apply the pipeline to the data
pipeline_clean_text.transform(test_str)

'mande para o email ou ou se inscreva no site'

Now that we have setted our pipeline, let's clean our datasets:

In [11]:
text_clean = df_text.apply(pipeline_clean_text.transform)
titles_clean = df_titles.apply(pipeline_clean_text.transform)
content_clean = df_content.apply(pipeline_clean_text.transform)

In [15]:
for txt in content_clean.sample(10, random_state=200):
    print(txt, '\n')

Tem alguma previsão para o início das aulas? 

Me interesso em DIM  GERENCIAMENTO E SEGURANCA EM REDES DE COMPUTADORES. Turnos vespertino ou noturno. 

up 

kkkkkkkkkkkkkkkkkkkkkkkkkk desculpe Anrafell 

IMD é INGLES TECNICO I ou Introdução à Internet das Coisas? 

Boa noite galera de TI! NOSSOS CANECOS FINALMENTE PRONTINHOS PARA DISTRIBUIÇÃO E sabe qual a melhor parte? Você prou o Projeto ReX festa de integração vai ter em primeira mão! A primeira distribuição dos canecos será durante o PROJETO REX Para aqueles que praram o caneco temos uma boa notícia ESTAREMOS VENDENDO NO PROJETO REX! CANECO  TIRANTE APENAS R  OBS Aqueles que não pegarem durante o integra ainda divulgaremos próxima o será o esquema para todo mundo pegar o caneco Confere o vídeo no insta no link abaixo para ver o resultado iradooooo dos nossos canecos 

Tenho interesse em participar quais os pré requisitos? 

Seria possível disponibilizar Desenvolvimento WEB ? 

Olá Any a página do curso no site do IMD é essa Lá no f

In [16]:
for txt in titles_clean.sample(10, random_state=200):
    print(txt, '\n')

Sugestão Salas de estudos divididas 

VTEX no IMD  UFRN 

Novas turmas criadas HOJE 

Processos de aproveitamento de estudos 

GRUPO PARA OS FORMANDOS 

Solicitação de Componente Curricular 

PROJETO DE EXTENSÃO  Oficina de Expressão Oral em Língua Inglesa 

Oportunidade de Bolsa 

Ferramentas para a disciplina IMD  MATEMÁTICA ELEMENTAR 

Novo Coordenador e Sala da Coordenação 



In [17]:
for txt in text_clean.sample(10, random_state=300):
    print(txt, '\n')

Nova Disciplina 

Fui assaltado também na minha primeira semana no IMD isso em  enquanto aguardava na parada próximo às residencias universitarias. Muito perigoso. 

Existe algum meio no SiGAA para conferir se o vínculo foi confirmado? 

Jefferson pode ser que para alguns alunos aconteça algum problema. Peço que tente novamente em outro PC e veja se a unidade está montada. Caso tenha algum problema procure o pessoal da TI na sala B. 

Obrigado. 

Obrigado Rubem. 

Pessoal eu fiz prova na sala A e esqueci minha garrafa dágua na sala. É uma garrafa de alumínio prateada. Se alguém encontrar por favor deixem na secretaria. Agradeço desde ja 

Cade as disciplinas na sexta N? Quem quer pagar no mínimo  matérias não consegue. 

 

Cine a SoftUrbano 



## Analysis

Let's do some a analysis of our clean datasets.

In [12]:
word_counts_content = content_clean.str.split().apply(len)
word_counts_titles = titles_clean.str.split().apply(len)
word_counts_text = text_clean.str.split().apply(len)

word_counts_content.describe()

count    11922.000000
mean        40.658027
std         68.105479
min          0.000000
25%          6.000000
50%         18.000000
75%         45.750000
max       1116.000000
Name: conteudo, dtype: float64

In [19]:
word_counts_titles.describe()

count    2711.000000
mean        6.478421
std         3.206226
min         1.000000
25%         4.000000
50%         6.000000
75%         8.000000
max        19.000000
Name: titulo, dtype: float64

In [20]:
word_counts_text.describe()

count    14633.000000
mean        34.325702
std         62.906446
min          0.000000
25%          5.000000
50%         12.000000
75%         36.000000
max       1116.000000
dtype: float64

You may have noticed that we have some empty content. Let's get rid of it.

In [13]:
indexDrop = []

for i in range(len(content_clean)):
    if len(content_clean[i]) == 0:
        indexDrop.append(i)

content_clean.drop(indexDrop, axis=0, inplace=True)
text_clean.drop(indexDrop, axis=0, inplace=True)

word_counts_content = content_clean.str.split().apply(len)
word_counts_text = text_clean.str.split().apply(len)

word_counts_content.describe()

count    11799.000000
mean        41.081871
std         68.332274
min          1.000000
25%          6.000000
50%         18.000000
75%         46.000000
max       1116.000000
Name: conteudo, dtype: float64

In [22]:
word_counts_text.describe()

count    14504.000000
mean        34.628654
std         63.103042
min          1.000000
25%          5.000000
50%         12.000000
75%         36.000000
max       1116.000000
dtype: float64

Luckily there wasn't much to get rid of. Now let's continue:

In [23]:
import plotly.graph_objects as go


def word_count_distr_graph(word_counts, title):
    # Plot
    fig = go.Figure(data=[go.Histogram(x=word_counts)])
    # add a title to center above the chart
    fig.update_layout(title_text=title, title_x=0.5)
    fig.show()

word_count_distr_graph(word_counts_text, 'Word count distribution in forum')

In [24]:
word_count_distr_graph(word_counts_titles, 'Word count distribution in titles')

In [25]:
word_count_distr_graph(word_counts_content, 'Word count distribution in messages')

It seems there are some words that appear very frequently in this dataset. Let's get an idea of what they are with Counter.

In [26]:
from collections import Counter
import plotly.graph_objects as go

def plot_histogram_word(text_list, n_most_common=30, title="text"):
    # create a list of words
    words = []
    for txt in text_list:
        words += txt.split()

    # count the number of times each word appears in the text
    word_counts = Counter(words)

    # select the top 30 most frequent words
    word_counts = dict(word_counts.most_common(n_most_common))

    # create a bar chart
    fig = go.Figure([go.Bar(x=list(word_counts.keys()), y=list(word_counts.values()))])
    fig.update_layout(title_text=f'Top {n_most_common} most frequent words in the {title}', title_x=0.5)
    fig.show()

plot_histogram_word(text_clean, 30, 'forum')
plot_histogram_word(titles_clean, 30, 'titles')
plot_histogram_word(content_clean, 30, 'messages')

There sure are a lot stop words we need to get rid of.  We'll use both spacy's and nltk's list for this:

In [14]:
import spacy
nlp = spacy.load('pt_core_news_sm')
stopwords_spacy = nlp.Defaults.stop_words
list(stopwords_spacy)[:10]

['ver',
 'disso',
 'nossas',
 'estava',
 'dentro',
 'pôde',
 'eles',
 'pelas',
 'duas',
 'saber']

In [15]:
import nltk

from nltk.corpus import stopwords
nltk.download('stopwords')
stopwords_nltk = stopwords.words('portuguese')

list(stopwords_nltk)[:10]

[nltk_data] Downloading package stopwords to /home/isaac/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


['a',
 'à',
 'ao',
 'aos',
 'aquela',
 'aquelas',
 'aquele',
 'aqueles',
 'aquilo',
 'as']

In [17]:
both_stopwords = set(stopwords_nltk) | set(stopwords_spacy)

In [19]:
def remove_stop_word(text):
    text = re.sub(r'[^\w\s]', '', text)

    tokens = text.split()

    tokens = filter(lambda token: token not in both_stopwords, tokens)

    return ' '.join(tokens)

We took advantage of this process to also remove non-alphanumeric characters from or token that are not going to be relevant. Let's see if we improved somewhat.

In [24]:
text_clean_no_stopwords = text_clean.apply(remove_stop_word)
titles_clean_no_stopwords = titles_clean.apply(remove_stop_word)
content_clean_no_stopwords = content_clean.apply(remove_stop_word)

In [27]:
plot_histogram_word(text_clean_no_stopwords, 30, 'forum')
plot_histogram_word(titles_clean_no_stopwords, 30, 'titles')
plot_histogram_word(content_clean_no_stopwords, 30, 'messages')

Some interesting things are showing up, but maybe it would have been more useful to have all text in lowercase before we remove stopwords (given the presence of such obvious stop words like 'A' and 'O').

In [28]:
text_clean_no_stopwords_lower = text_clean.str.lower().apply(remove_stop_word)
titles_clean_no_stopwords_lower = titles_clean.str.lower().apply(remove_stop_word)
content_clean_no_stopwords_lower = content_clean.str.lower().apply(remove_stop_word)


plot_histogram_word(text_clean_no_stopwords_lower, 30, 'forum')
plot_histogram_word(titles_clean_no_stopwords_lower, 30, 'titles')
plot_histogram_word(content_clean_no_stopwords_lower, 30, 'messsages')

That's better, but now we can see we're getting some extra information that might not be all that useful for now. Is the difference between 'disciplina' and 'disciplinas' particularly important for what we want right now? What about 'interesse' or 'interessado'?

It seems in this case lemmatizing might be a good idea.

We can now do some lemmatizing:

In [29]:
def spacy_lemmatizer(text):
    doc = nlp(text)

    txt = [token.lemma_ for token in doc]

    txt = [word for word in txt if len(word) > 2]

    return ' '.join(txt)


(This might take some minutes):

In [30]:
text_clean_lemmatized = text_clean_no_stopwords_lower.apply(spacy_lemmatizer)

Same to just titles:

In [31]:

titles_clean_lemmatized = titles_clean_no_stopwords_lower.apply(spacy_lemmatizer)

Same for titles concat messages:

In [32]:
content_clean_lemmatized = content_clean_no_stopwords_lower.apply(spacy_lemmatizer)

With our lemmatizing done, let's check our histograms again

In [33]:
plot_histogram_word(text_clean_lemmatized, 30, 'forum')
plot_histogram_word(titles_clean_lemmatized, 30, 'titles')
plot_histogram_word(content_clean_lemmatized, 30, 'messages')

Let's also check the bigrams and see if we get anything of interest.

In [34]:
import nltk
nltk.download('punkt')
from collections import Counter
from nltk.util import ngrams
from nltk.tokenize import word_tokenize
import plotly.graph_objs as go

# Defining the function to generate n-grams
def generate_ngrams(text, n, lowercase=False):
    if lowercase:
        text = text.lower()

    n_grams = ngrams(nltk.word_tokenize(text), n)
    return [ ' '.join(grams) for grams in n_grams]


def plot_n_grams(dataset, n_most_common=30, n=2, title='text'):
    n_grams_counter = Counter()

    # Loop through each text in the training set
    for text in dataset.values:
        # Call the function to generate bigrams
        n_grams_counter.update(generate_ngrams(text, n, lowercase=True))

    # select the top 30 most frequent words
    n_grams_counter = dict(n_grams_counter.most_common(n_most_common))

    # create a bar chart
    fig = go.Figure([go.Bar(x=list(n_grams_counter.keys()), y=list(n_grams_counter.values()))])
    fig.update_layout(title_text=f'Top {n_most_common} most frequent bigrams in the {title}')
    fig.show()

[nltk_data] Downloading package punkt to /home/isaac/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [35]:
plot_n_grams(text_clean_lemmatized, title='forum')
plot_n_grams(titles_clean_lemmatized, title='titles')
plot_n_grams(content_clean_lemmatized, title='messages')

It appears that while lemmatizing does get rid of some unecessary data, it also interferes with some relevant information (such as transforming 'dado', which means data, into 'dar', which means to give).

Let's filter out words with less than 3 characters of our non-lemmatized datasets and compare the results

In [36]:
def remove_less_than_three(text):
    tokens = [token for token in text.split() if len(token)>2]

    return ' '.join(tokens)

In [37]:
text_clean_reduce = text_clean_no_stopwords_lower.apply(remove_less_than_three)
titles_clean_reduce = titles_clean_no_stopwords_lower.apply(remove_less_than_three)
content_clean_reduce = content_clean_no_stopwords_lower.apply(remove_less_than_three)

In [38]:
plot_histogram_word(text_clean_reduce, 30, 'forum')
plot_histogram_word(titles_clean_reduce, 30, 'titles')
plot_histogram_word(content_clean_reduce, 30, 'messages')

In [39]:
plot_n_grams(text_clean_reduce, title='forum')
plot_n_grams(titles_clean_reduce, title='titles')
plot_n_grams(content_clean_reduce, title='messages')

Well, that's certainly better. It seems a certain subject might be frequently mentioned in our forum. let's check our trigrams to confirm it:

In [40]:
plot_n_grams(text_clean_reduce, title='forum', n=3)
plot_n_grams(titles_clean_reduce, title='titles', n=3)
plot_n_grams(content_clean_reduce, title='messages', n=3)

Yes, it is indeed cited ver frequently (even if most topics don't seen to be titled after it). Another thing of note in this dataset is the name 'helena velcic maziviero' which is showing up as a frequent trigram. Sure enough, this person seems to have had at some point an habit of signing of their messages with their name, and they have posted a lot on this forum.

All in all, the forum seems to have mostly been used as expected. Discussions of subjects, hours, the course itself, and internship and work opportunities seem to be the most frequent topics in it. In special, the most frequent subject is "Fundamentos Matemáticos da Computação".

Now we se TF-IDF to represent our datasets.

In [41]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer_titles = TfidfVectorizer()
vectorizer_titles.fit(titles_clean_reduce)
titles_matrix = vectorizer_titles.transform(titles_clean_reduce).toarray()
titles_tfidf = pd.DataFrame(titles_matrix, columns=vectorizer_titles.get_feature_names_out(), index=titles_clean_reduce)

vectorizer_content = TfidfVectorizer()
vectorizer_content.fit(content_clean_reduce)
content_matrix = vectorizer_content.transform(content_clean_reduce).toarray()
content_tfidf = pd.DataFrame(content_matrix, columns=vectorizer_content.get_feature_names_out(), index=content_clean_reduce)

vectorizer_text = TfidfVectorizer()
vectorizer_text.fit(text_clean_reduce)
text_matrix = vectorizer_text.transform(text_clean_reduce).toarray()
text_tfidf = pd.DataFrame(text_matrix, columns=vectorizer_text.get_feature_names_out(), index=text_clean_reduce)

titles_tfidf

aaa  abaixo  \
titulo                                                            
curso férias pet resolução problemas matemática...  0.0     0.0   
cursos férias linux git                             0.0     0.0   
possibilidade turmas bti sábados                    0.0     0.0   
maratona feminina programação                       0.0     0.0   
contratação substituto turma banco dados            0.0     0.0   
...                                                 ...     ...   
disciplinas equivalentes                            0.0     0.0   
boas vindas semestre                                0.0     0.0   
horário aulas turmas imd                            0.0     0.0   
secretaria coordenação                              0.0     0.0   
msdn academic alliance                              0.0     0.0   

                                                    abaixoassinado  aberta  \
titulo                                                                       
curso férias pet resolução problemas matemática...             0.0     0.0   
cursos férias linux git                                        0.0     0.0   
possibilidade turmas bti sábados                               0.0     0.0   
maratona feminina programação                                  0.0     0.0   
contratação substituto turma banco dados                       0.0     0.0   
...                                                            ...     ...   
disciplinas equivalentes                                       0.0     0.0   
boas vindas semestre                                           0.0     0.0   
horário aulas turmas imd                                       0.0     0.0   
secretaria coordenação                                         0.0     0.0   
msdn academic alliance                                         0.0     0.0   

                                                    abertas  aberto  abertos  \
titulo                                                                         
curso férias pet resolução problemas matemática...      0.0     0.0      0.0   
cursos férias linux git                                 0.0     0.0      0.0   
possibilidade turmas bti sábados                        0.0     0.0      0.0   
maratona feminina programação                           0.0     0.0      0.0   
contratação substituto turma banco dados                0.0     0.0      0.0   
...                                                     ...     ...      ...   
disciplinas equivalentes                                0.0     0.0      0.0   
boas vindas semestre                                    0.0     0.0      0.0   
horário aulas turmas imd                                0.0     0.0      0.0   
secretaria coordenação                                  0.0     0.0      0.0   
msdn academic alliance                                  0.0     0.0      0.0   

                                                    abertura  abre  abril  \
titulo                                                                      
curso férias pet resolução problemas matemática...       0.0   0.0    0.0   
cursos férias linux git                                  0.0   0.0    0.0   
possibilidade turmas bti sábados                         0.0   0.0    0.0   
maratona feminina programação                            0.0   0.0    0.0   
contratação substituto turma banco dados                 0.0   0.0    0.0   
...                                                      ...   ...    ...   
disciplinas equivalentes                                 0.0   0.0    0.0   
boas vindas semestre                                     0.0   0.0    0.0   
horário aulas turmas imd                                 0.0   0.0    0.0   
secretaria coordenação                                   0.0   0.0    0.0   
msdn academic alliance                                   0.0   0.0    0.0   

                                                    ...  ícone  índices  \
titulo                                         

In [42]:
from sklearn.decomposition import TruncatedSVD

# LSA para Títulos
lsa_titles = TruncatedSVD(n_components=5)
lsa_titles.fit(titles_matrix)

# LSA para Conteúdo
lsa_content = TruncatedSVD(n_components=5)
lsa_content.fit(content_matrix)

# LSA para Texto Completo
lsa_text = TruncatedSVD(n_components=5)
lsa_text.fit(text_matrix)


TruncatedSVD(n_components=5)

In [43]:
def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        message = "Topic #%d: " % topic_idx
        message += " ".join([feature_names[i] for i in topic.argsort()[:-n_top_words - 1:-1]])
        print(message)

# Imprimir tópicos para títulos
print("By titles:")
print_top_words(lsa_titles, vectorizer_titles.get_feature_names_out(), 10)

# Imprimir tópicos para conteúdo
print("By titles:")
print_top_words(lsa_content, vectorizer_content.get_feature_names_out(), 10)

# Imprimir tópicos para texto completo
print("By titles:")
print_top_words(lsa_text, vectorizer_text.get_feature_names_out(), 10)


By titles:
Topic #0: oportunidade estágio bolsa vaga imd proficiência técnico solicitações seleção desenvolvimento
Topic #1: imd proficiência solicitações prova resultado realização disciplinas inglês disciplina sistemas
Topic #2: bti secretaria funcionamento eleição coordenação bcc disciplinas discente colegiado alunos
Topic #3: vaga estágio desenvolvedor bti sistemas web secretaria funcionamento programador desenvolvimento
Topic #4: disciplinas turmas seleção portal vaga monitoria imd oferta tópicos disciplina
By titles:
Topic #0: interesse participar turma noturno edb integral disciplina alguém curso imd
Topic #1: dim imd sistemas disciplina turma programação disciplinas computação alunos dados
Topic #2: dim projeto grafos matemáticos fundamentos iii computação programação linguagens computadores
Topic #3: anexo dim edital informações segue computação inscrições projeto arquivo cartaz
Topic #4: imd sistemas dados operacionais banco computadores anexo linguagem deferidos básicas
By t

In [44]:
from sklearn.feature_extraction.text import TfidfVectorizer
import pandas as pd


vectorizer_titles = TfidfVectorizer (max_features=10000)
titles_matrix = vectorizer_titles.fit_transform(titles_clean_reduce)
titles_tfidf = pd.DataFrame(titles_matrix.toarray(), columns=vectorizer_titles.get_feature_names_out(), index=range(len(titles_clean_reduce)))

vectorizer_content = TfidfVectorizer(max_features=10000)
content_matrix = vectorizer_content.fit_transform(content_clean_reduce)
content_tfidf = pd.DataFrame(content_matrix.toarray(), columns=vectorizer_content.get_feature_names_out(), index=range(len(content_clean_reduce)))

vectorizer_text = TfidfVectorizer(max_features=10000)
text_matrix = vectorizer_text.fit_transform(text_clean_reduce)
text_tfidf = pd.DataFrame(text_matrix.toarray(), columns=vectorizer_text.get_feature_names_out(), index=range(len(text_clean_reduce)))

# Exibindo o DataFrame dos títulos
print(titles_tfidf.head())


   aaa  abaixo  abaixoassinado  aberta  abertas  aberto  abertos  abertura  \
0  0.0     0.0             0.0     0.0      0.0     0.0      0.0       0.0   
1  0.0     0.0             0.0     0.0      0.0     0.0      0.0       0.0   
2  0.0     0.0             0.0     0.0      0.0     0.0      0.0       0.0   
3  0.0     0.0             0.0     0.0      0.0     0.0      0.0       0.0   
4  0.0     0.0             0.0     0.0      0.0     0.0      0.0       0.0   

   abre  abril  ...  ícone  índices  óculos  óptica  órgãos  ônibus  última  \
0   0.0    0.0  ...    0.0      0.0     0.0     0.0     0.0     0.0     0.0   
1   0.0    0.0  ...    0.0      0.0     0.0     0.0     0.0     0.0     0.0   
2   0.0    0.0  ...    0.0      0.0     0.0     0.0     0.0     0.0     0.0   
3   0.0    0.0  ...    0.0      0.0     0.0     0.0     0.0     0.0     0.0   
4   0.0    0.0  ...    0.0      0.0     0.0     0.0     0.0     0.0     0.0   

   últimos  única  único  
0      0.0    0.0    0.0  
1 

In [45]:
from sklearn.decomposition import NMF

# Aplicando NMF ao texto completo para extrair tópicos
nmf_model = NMF(n_components=5, init='random', random_state=0)
nmf_topics = nmf_model.fit_transform(text_matrix)  # Usando a matriz TF-IDF do texto completo

# Função para exibir os tópicos
def display_topics(model, feature_names, no_top_words):
    for topic_idx, topic in enumerate(model.components_):
        print(f"Topic {topic_idx}:")
        print(" ".join([feature_names[i] for i in topic.argsort()[:-no_top_words - 1:-1]]))

# Exibindo tópicos
display_topics(nmf_model, vectorizer_text.get_feature_names_out(), 10)


Topic 0:
imd proficiência sistemas dados operacionais programação computadores banco solicitações prova
Topic 1:
turma disciplinas alunos curso turmas semestre dia bti professor disciplina
Topic 2:
interesse participar noturno edb integral turma grafos mudar alguém turno
Topic 3:
dim projeto computação programação software grafos matemáticos fundamentos iii linguagens
Topic 4:
anexo edital informações segue inscrições cartaz detalhes arquivo obs documento


In [46]:
from bertopic import BERTopic
from bertopic.vectorizers import ClassTfidfTransformer
from bertopic.representation import MaximalMarginalRelevance
from sklearn.feature_extraction.text import CountVectorizer

from sklearn.pipeline import make_pipeline
from sklearn.decomposition import TruncatedSVD
from sklearn.feature_extraction.text import TfidfVectorizer
import re

In [47]:
pipe = make_pipeline(
    TfidfVectorizer(stop_words=list(both_stopwords), max_features=10000, ngram_range=(2, 2)),
    TruncatedSVD(1024)
)

topic_model_titles = BERTopic(embedding_model=pipe, nr_topics=20) # We set a maximum number of topics to avoid a mess
topic_model_content = BERTopic(embedding_model=pipe, nr_topics=20) # We set a maximum number of topics to avoid a mess

docs_titles = df['titulo']
docs_content = df['conteudo']

docs_titles = [re.sub(r'[^a-zA-Z\s]', ' ', doc) for doc in docs_titles] # remove numbers and punctuation
docs_content = [re.sub(r'[^a-zA-Z\s]', ' ', doc) for doc in docs_content] # remove numbers and punctuation

topics_titles, probs_titles = topic_model_titles.fit_transform(docs_titles)
topics_content, probs_content = topic_model_content.fit_transform(docs_content)

In [48]:
topic_model_titles.get_topic_info()

Topic  Count                                      Name  \
0      -1   1729                            -1_de_da_do_em   
1       0   7630                           0_de_para_do_em   
2       1    928                   1_turmas_rias_sobre_ead   
3       2    492  2_formandos_indeferidos_camisa_camisetas   
4       3    417                   3_gios_da_percurso_html   
5       4    166   4_academic_msdn_alliance_acessibilidade   
6       5     91               5_boleiros_peladeiros_aten_   
7       6     72                  6_indeferimentos_no_bti_   
8       7     66              7_insatisfa_um_mais_semestre   
9       8     46                     8_facebook_grupos_do_   
10      9     43          9_participacao_confirm_evento_no   
11     10     39                     10_grade_curricular__   
12     11     37          11_pelas_brancas_substitui_vidro   
13     12     37              12_materia_indeferimento_de_   
14     13     33                    13_optativas_noturno__   
15     14     23   14_probabilidade_infer_equivalente_mais   
16     15     23                15_proximo_assaltos_ao_imd   
17     16     23               16_avisos_semana_aula_sobre   
18     17     14                        17_rumores_fmcii__   
19     18     13                18_coursera_pareceria_com_   

                                       Representation  \
0   [de, da, do, em, para, no, sobre, como, na, ufrn]   
1   [de, para, do, em, imd, bti, ncia, disciplinas...   
2   [turmas, rias, sobre, ead, da, cursos, recente...   
3   [formandos, indeferidos, camisa, camisetas, fm...   
4   [gios, da, percurso, html, num, fmciii, css, d...   
5   [academic, msdn, alliance, acessibilidade, cpi...   
6          [boleiros, peladeiros, aten, , , , , , , ]   
7             [indeferimentos, no, bti, , , , , , , ]   
8       [insatisfa, um, mais, semestre, de, , , , , ]   
9                [facebook, grupos, do, , , , , , , ]   
10    [participacao, confirm, evento, no, , , , , , ]   
11                [grade, curricular, , , , , , , , ]   
12  [pelas, brancas, substitui, vidro, lousas, das...   
13         [materia, indeferimento, de, , , , , , , ]   
14               [optativas, noturno, , , , , , , , ]   
15  [probabilidade, infer, equivalente, mais, ncia...   
16           [proximo, assaltos, ao, imd, , , , , , ]   
17        [avisos, semana, aula, sobre, de, , , , , ]   
18                   [rumores, fmcii, , , , , , , , ]   
19           [coursera, pareceria, com, , , , , , , ]   

                                  Representative_Docs  
0   [Disciplina de T picos em Projeto de Inova  o,...  
1   [Demandas de disciplinas para o BCC e BTI    n...  
2   [A respeito da reuni o recente sobre a reforma...  
3     [Formandos       , Formandos       , Formandos]  
4   [ URGENTE  Demanda de Grafos  C lculo num rico...  
5   [Participa  o na Comiss o Permanente de Inclus...  
6   [ATEN  O  BOLEIROS    PELADEIROS     , ATEN  O...  
7   [Indeferimentos no BTI, Indeferimentos no BTI,...  
8   [Mais um semestre de insatisfa  o, Mais um sem...  
9   [GRUPOS DO FACEBOOK, GRUPOS DO FACEBOOK, GRUPO...  
10  [Participacao no evento confIRM, Participacao ...  
11  [Grade Curricular, Grade Curricular, Grade Cur...  
12  [Substitui  o das lousas brancas pelas de vidr...  
13  [Indeferimento de materia, Indeferimento de ma...  
14  [Optativas noturno, Optativas noturno, Optativ...  
15  [Probabilidade   Infer ncia n o    mais  equiv...  
16  [ASSALTOS PROXIMO AO IMD, ASSALTOS PROXIMO AO ...  
17  [Avisos sobre  a semana de aula, Avisos sobre ...  
18  [Rumores   FMCII, Rumores   FMCII, Rumores   F...  
19  [Pareceria com Coursera, Pareceria com Courser...

In [49]:
topic_model_content.get_topic_info()

Topic  Count                                             Name  \
0      -1    825                                 -1_de_do_em_para   
1       0   5119                         0_up_que_tenho_interesse   
2       1   4733                                  1_de_para_do_em   
3       2    188                               2_poss_vel_que_dio   
4       3    182                        3_formul_rio_question_que   
5       4    153                   4_noturno_turno_contato_entrar   
6       5    136                                5_turma_lp_edb_de   
7       6    114                              6_que_do_bti_alunos   
8       7    108                         7_turmas_ead_obrigat_que   
9       8    101                   8_disciplina_co_requisitos_que   
10      9     52                            9_hoje_aula_voc_amanh   
11     10     44  10_complementares_atividades_quantifiers_presen   
12     11     33                        11_planos_drive_itp_turma   
13     12     28               12_normal_motos_estacionamento_wvc   
14     13     22                   13_ncias_ci_institucional_mail   
15     14     22                   14_circuitos_gicos_introdu_dim   
16     15     20                15_tempor_que_garrafa_calculadora   
17     16     17                    16_the_quest_erasmus_rosemary   
18     17     13                   17_novidade_alguma_sobre_ciclo   
19     18     12                        18_aula_sala_protestos_pq   

                                       Representation  \
0       [de, do, em, para, da, que, com, no, es, ser]   
1   [up, que, tenho, interesse, tamb, se, obrigado...   
2       [de, para, do, em, da, que, com, no, es, imd]   
3   [poss, vel, que, dio, de, pr, do, para, no, ap...   
4   [formul, rio, question, que, para, de, um, do,...   
5   [noturno, turno, contato, entrar, algu, integr...   
6   [turma, lp, edb, de, que, turmas, professor, r...   
7   [que, do, bti, alunos, not, cia, de, dispon, n...   
8   [turmas, ead, obrigat, que, rias, disciplinas,...   
9   [disciplina, co, requisitos, que, requisito, p...   
10  [hoje, aula, voc, amanh, que, com, se, de, sil...   
11  [complementares, atividades, quantifiers, pres...   
12  [planos, drive, itp, turma, sharing, folders, ...   
13  [normal, motos, estacionamento, wvc, aula, um,...   
14  [ncias, ci, institucional, mail, alunas, de, n...   
15  [circuitos, gicos, introdu, dim, camisa, bti, ...   
16  [tempor, que, garrafa, calculadora, plenaria, ...   
17  [the, quest, erasmus, rosemary, mundus, monaha...   
18  [novidade, alguma, sobre, ciclo, segundo, list...   
19  [aula, sala, protestos, pq, hoje, na, feito, f...   

                                  Representative_Docs  
0   [O Instituto Metr pole Digital  IMD UFRN  est ...  
1                                  [up\n, UP\n, up\n]  
2   [O projeto intitulado  Tecnologia da Informa  ...  
3   [Segundo a PROGRAD  aqui est o as respostas pa...  
4   [O formul rio Consulta de Demanda para        ...  
5   [Sou do turno integral e tenho interesse em mu...  
6   [Tenho interesse na turma de LP \n, ol  pessoa...  
7   [Prezados Colegas \n\nCaso algu m na disciplin...  
8   [Ol   Eliabe \nOlha  a suspens o dos jubilamen...  
9   [tamb m tive o mesmo problema do sistema offli...  
10  [N o haver  aula hoje para turma  H \n, Os alu...  
11  [Segue a lista de presen a da divulga  o das  ...  
12  [Pessoal \n\nEssa   a lista de componentes ofe...  
13  [Chamada para participa  o  XIII Workshop de V...  
14  [Atrav s do Programa de Est gio  o Grupo Neoen...  
15  [DIM      INTRODU  O A CIRCUITOS L GICOS\n, \n...  
16  [Bom dia gente \nNo link abaixo o Frederico Ma...  
17  [Segue a lista dos aprovados \n\n           PE...  
18  [Alguma novidade sobre a reforma \n, Alguma no...  
19  [Pessoal  a professora disse hoje em sala de a...

In [50]:
for idx in range(len(topic_model_titles.get_topic_info())):
    print(f'Relevant words - topic {idx}:')
    print(topic_model_titles.get_topic(idx))
    print()

Relevant words - topic 0:
[('de', 0.045514209672997165), ('para', 0.03501785521730413), ('do', 0.02739807342172637), ('em', 0.025442662432125153), ('imd', 0.023992431407928685), ('bti', 0.023486028224981796), ('ncia', 0.023192530747823556), ('disciplinas', 0.021839304926157755), ('bcc', 0.020182035482565586), ('profici', 0.019867213428519867)]

Relevant words - topic 1:
[('turmas', 0.07871246042889955), ('rias', 0.048076562146044464), ('sobre', 0.047980865647104944), ('ead', 0.047108554037404445), ('da', 0.044130723184836095), ('cursos', 0.042403894502098), ('recente', 0.04050383659555341), ('adas', 0.03845223410800574), ('respeito', 0.03809434637395474), ('sem', 0.0379555114091697)]

Relevant words - topic 2:
[('formandos', 0.4650520949620388), ('indeferidos', 0.3403438108994987), ('camisa', 0.2775549514144682), ('camisetas', 0.2625903193424761), ('fmc', 0.1601603235690083), ('basquete', 0.13215856173260074), ('vai', 0.11198707706479828), ('quando', 0.10741481226085763), ('tomadas', 0

In [51]:
for idx in range(len(topic_model_content.get_topic_info())):
    print(f'Relevant words - topic {idx}:')
    print(topic_model_content.get_topic(idx))
    print()

Relevant words - topic 0:
[('up', 0.06766851853714248), ('que', 0.03397608630767479), ('tenho', 0.03372790160340781), ('interesse', 0.02894861992574284), ('tamb', 0.027521286786069715), ('se', 0.023288389044488014), ('obrigado', 0.02309546792260879), ('eu', 0.022105089196647196), ('no', 0.020794769706068902), ('pra', 0.01876997512183087)]

Relevant words - topic 1:
[('de', 0.03888716914317435), ('para', 0.024703886021098433), ('do', 0.024090830841844543), ('em', 0.022731746328578918), ('da', 0.022664013739447673), ('que', 0.02216348349634097), ('com', 0.01934884061839639), ('no', 0.019279730014143667), ('es', 0.017636335621181772), ('imd', 0.015718632087258225)]

Relevant words - topic 2:
[('poss', 0.04261711373483117), ('vel', 0.034254959969811295), ('que', 0.03401451207001584), ('dio', 0.03184290468514668), ('de', 0.029321023348544396), ('pr', 0.027219434492911674), ('do', 0.02625093971024964), ('para', 0.02369901684413591), ('no', 0.022547303405251455), ('aproveitamento', 0.02003413

In [52]:
topic_model_titles.visualize_barchart(n_words=8, top_n_topics=50, width=500, height=500, title='titles')

In [53]:
topic_model_content.visualize_barchart(n_words=8, top_n_topics=50, width=500, height=500, title='content')

In [54]:
# Run this only during class
# Run the visualization with the original embeddings
topic_model_titles.visualize_documents(docs_titles)


In [55]:
topic_model_content.visualize_documents(docs_content)

In [ ]:
import os
import getpass
from langchain_openai import ChatOpenAI, OpenAIEmbeddings

os.environ['OPENAI_API_KEY'] = getpass.getpass('OpenAI API Key:')

# Inicializar o cliente OpenAI
openai_client = ChatOpenAI(model='gpt-3.5-turbo-16k')
max_tokens = 8192  # o máximo para text-embedding-3-large é 8192


OpenAI API Key:··········


In [ ]:
print(openai_client.get_num_tokens(('Eu gosto de farofa')))

7


In [ ]:
# check if any text is longer than max_tokens. That's definitely not our case, but it's good to know.
long_texts_titles = [text for text in df['titulo'] if openai_client.get_num_tokens(text) > max_tokens]
long_texts_content = [text for text in df['conteudo'] if openai_client.get_num_tokens(text) > max_tokens]
print(f'Number of texts longer than {max_tokens} tokens: {len(long_texts_titles)} (reasons) and {len(long_texts_content)} (challenges)')

Number of texts longer than 8192 tokens: 0 (reasons) and 0 (challenges)


In [ ]:
# According to openai pricing website, the cost of the embedding API is $0.00013 per 1000 tokens
# https://openai.com/pricing/

from typing import List

def calculate_total_cost(text_list: List[str], cost_per_thousand_tokens: float) -> float:
    """
    This function calculates the total cost of processing a list of texts,
    based on a cost per thousand tokens.

    Args:
        text_list (List[str]): A list of texts to be processed.
        cost_per_thousand_tokens (float): The cost of processing a thousand tokens.

    Returns:
        float: The total cost of processing the texts.
    """
    # Initialize the total number of tokens
    total_token_count = 0

    # Iterate over each text in the list
    for text in text_list:
        # Use the OpenAI client to get the number of tokens in the text
        # and add it to the total token count
        total_token_count += openai_client.get_num_tokens(text)

    # Calculate the total cost by multiplying the total token count by the cost per thousand tokens
    # and dividing by 1000 (since the cost is per thousand tokens)
    total_cost = total_token_count * cost_per_thousand_tokens / 1000

    return total_cost

all_texts_concat = df['titulo'].values.tolist() + df['conteudo'].values.tolist()

print(f'Cost of embedding API for {len(all_texts_concat)} texts: ${calculate_total_cost(all_texts_concat, 0.00013):.4f} USD')

Cost of embedding API for 23844 texts: $0.1508 USD


In [ ]:

openai_embeddings = OpenAIEmbeddings(model='text-embedding-3-large', dimensions=3072)

embeddings_titles = openai_embeddings.embed_documents(df['titulo'].values.tolist())
embeddings_content = openai_embeddings.embed_documents(df['conteudo'].values.tolist())

In [11]:
embeddings_df_titles = pd.Series(embeddings_titles).to_frame()
embeddings_df_content = pd.Series(embeddings_content).to_frame()
embeddings_df_titles.columns = ['openai_embedding_title']
embeddings_df_content.columns = ['openai_embedding_content']

In [12]:
df_titles = pd.concat([df, embeddings_df_titles], axis=1)

titulo        data  \
0      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
1      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
2      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
3      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
4      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
...                                                  ...         ...   
11917                             MSDN Academic Alliance  26/01/2013   
11918                             MSDN Academic Alliance  26/01/2013   
11919                             MSDN Academic Alliance  26/01/2013   
11920                             MSDN Academic Alliance  27/01/2013   
11921                             MSDN Academic Alliance  28/01/2013   

           hora                                    nome  \
0      12:14:06         MARINA MEDEIROS DE ARAÚJO LEITE   
1      13:47:55               RAMON OLIVEIRA DE ALMEIDA   
2      14:09:01  ANDRIEL VINICIUS DE MEDEIROS FERNANDES   
3      15:15:12          GABRIEL CARVALHO PEREIRA SILVA   
4      15:26:24           HIRANILSON ANDRADE DOS SANTOS   
...         ...                                     ...   
11917  12:27:04        CEPHAS ALVES DA SILVEIRA BARRETO   
11918  16:58:11              AVANDO JOSE DE LIMA CAMPOS   
11919  18:11:29                        PABLO NUNES DIAS   
11920  21:09:49              AVANDO JOSE DE LIMA CAMPOS   
11921  14:16:18        CEPHAS ALVES DA SILVEIRA BARRETO   

                                                conteudo  \
0      Nós do PET CC queremos saber qual é o interess...   
1      Se der pra participar deste e do outro(linux +...   
2                                      Tenho interesse\n   
3                                      tenho interesse\n   
4                tenho interesse se for no formato ead\n   
...                                                  ...   
11917  vou defender ninguem...mas além de torcer para...   
11918  Galera... calma!\nO curso ainda nem começou e ...   
11919  então vamos deletar os comments mais pesados, ...   
11920                                          cobrar*\n   
11921  Não é uma questão de " o aluno pagar sempre", ...   

                                  openai_embedding_title  
0      [-0.027457306857366456, 0.02476463361645097, -...  
1      [-0.02742825789430224, 0.025107200899435186, -...  
2      [-0.02742825789430224, 0.025107200899435186, -...  
3      [-0.027457306857366456, 0.02476463361645097, -...  
4      [-0.02742825789430224, 0.025107200899435186, -...  
...                                                  ...  
11917  [-0.02038712625526558, 0.038987752284273265, -...  
11918  [-0.02084117724943331, 0.038957103519552796, -...  
11919  [-0.02038712625526558, 0.038987752284273265, -...  
11920  [-0.02080768598349044, 0.03895981359554759, -0...  
11921  [-0.020845880028446263, 0.03893094750987262, -...  

[11922 rows x 6 columns]

In [15]:
df_with_embeddings = pd.concat([df_titles, embeddings_df_content], axis=1)
df_with_embeddings

titulo        data  \
0      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
1      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
2      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
3      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
4      Curso de Férias do PET CC: Resolução de Proble...  04/04/2024   
...                                                  ...         ...   
11917                             MSDN Academic Alliance  26/01/2013   
11918                             MSDN Academic Alliance  26/01/2013   
11919                             MSDN Academic Alliance  26/01/2013   
11920                             MSDN Academic Alliance  27/01/2013   
11921                             MSDN Academic Alliance  28/01/2013   

           hora                                    nome  \
0      12:14:06         MARINA MEDEIROS DE ARAÚJO LEITE   
1      13:47:55               RAMON OLIVEIRA DE ALMEIDA   
2      14:09:01  ANDRIEL VINICIUS DE MEDEIROS FERNANDES   
3      15:15:12          GABRIEL CARVALHO PEREIRA SILVA   
4      15:26:24           HIRANILSON ANDRADE DOS SANTOS   
...         ...                                     ...   
11917  12:27:04        CEPHAS ALVES DA SILVEIRA BARRETO   
11918  16:58:11              AVANDO JOSE DE LIMA CAMPOS   
11919  18:11:29                        PABLO NUNES DIAS   
11920  21:09:49              AVANDO JOSE DE LIMA CAMPOS   
11921  14:16:18        CEPHAS ALVES DA SILVEIRA BARRETO   

                                                conteudo  \
0      Nós do PET CC queremos saber qual é o interess...   
1      Se der pra participar deste e do outro(linux +...   
2                                      Tenho interesse\n   
3                                      tenho interesse\n   
4                tenho interesse se for no formato ead\n   
...                                                  ...   
11917  vou defender ninguem...mas além de torcer para...   
11918  Galera... calma!\nO curso ainda nem começou e ...   
11919  então vamos deletar os comments mais pesados, ...   
11920                                          cobrar*\n   
11921  Não é uma questão de " o aluno pagar sempre", ...   

                                  openai_embedding_title  \
0      [-0.027457306857366456, 0.02476463361645097, -...   
1      [-0.02742825789430224, 0.025107200899435186, -...   
2      [-0.02742825789430224, 0.025107200899435186, -...   
3      [-0.027457306857366456, 0.02476463361645097, -...   
4      [-0.02742825789430224, 0.025107200899435186, -...   
...                                                  ...   
11917  [-0.02038712625526558, 0.038987752284273265, -...   
11918  [-0.02084117724943331, 0.038957103519552796, -...   
11919  [-0.02038712625526558, 0.038987752284273265, -...   
11920  [-0.02080768598349044, 0.03895981359554759, -0...   
11921  [-0.020845880028446263, 0.03893094750987262, -...   

                                openai_embedding_content  
0      [-0.05679389974205168, 0.017046191217883602, -...  
1      [-0.036802685092645185, 0.04976309611689826, -...  
2      [-0.05551405725778837, 0.0347559346698138, -0....  
3      [-0.05309777223857962, 0.03476904260297789, -0...  
4      [-0.05553957220949017, 0.013698228995155694, -...  
...                                                  ...  
11917  [0.0032409552946556825, 0.04669262840788457, -...  
11918  [-0.010667573818760039, 0.012210832158453911, ...  
11919  [-0.05125453116286171, 0.004992481585284158, -...  
11920  [-0.022340873001297393, 0.04255715709028035, -...  
11921  [-0.03625538358957027, 0.037232616584219745, -...  

[11922 rows x 7 columns]

## Now I will use our dataset with OpenAI Embeddings

In [1]:
import pandas as pd

df = pd.read_json('dataset/data.json')

df.head()

titulo        data      hora  \
0  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  12:14:06   
1  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  13:47:55   
2  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  14:09:01   
3  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  15:15:12   
4  Curso de Férias do PET CC: Resolução de Proble...  04/04/2024  15:26:24   

                                     nome  \
0         MARINA MEDEIROS DE ARAÚJO LEITE   
1               RAMON OLIVEIRA DE ALMEIDA   
2  ANDRIEL VINICIUS DE MEDEIROS FERNANDES   
3          GABRIEL CARVALHO PEREIRA SILVA   
4           HIRANILSON ANDRADE DOS SANTOS   

                                            conteudo  \
0  Nós do PET CC queremos saber qual é o interess...   
1  Se der pra participar deste e do outro(linux +...   
2                                  Tenho interesse\n   
3                                  tenho interesse\n   
4            tenho interesse se for no formato ead\n   

                              openai_embedding_title  \
0  [-0.027457306900000002, 0.024764633600000002, ...   
1  [-0.027428257900000003, 0.0251072009, -0.02079...   
2  [-0.027428257900000003, 0.0251072009, -0.02079...   
3  [-0.027457306900000002, 0.024764633600000002, ...   
4  [-0.027428257900000003, 0.0251072009, -0.02079...   

                            openai_embedding_content  
0  [-0.056793899700000004, 0.0170461912, -0.02367...  
1  [-0.0368026851, 0.0497630961, -0.0215803114, -...  
2  [-0.0555140573, 0.034755934700000005, -0.01257...  
3  [-0.053097772200000004, 0.0347690426, -0.01537...  
4  [-0.055539572200000005, 0.013698229000000001, ...

In [2]:
import nltk
import spacy

from nltk.corpus import stopwords
nltk.download('stopwords')
stopwords_nltk = stopwords.words('portuguese')

nlp = spacy.load('pt_core_news_sm')
stopwords_spacy = nlp.Defaults.stop_words

both_stopwords = set(stopwords_nltk) | set(stopwords_spacy)

[nltk_data] Downloading package stopwords to /home/isaac/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
from bertopic import BERTopic
from bertopic.vectorizers import ClassTfidfTransformer
from bertopic.representation import MaximalMarginalRelevance
from sklearn.feature_extraction.text import CountVectorizer

vectorizer_model_title = CountVectorizer(stop_words=list(both_stopwords), ngram_range=(2,2))
ctfidf_model_title = ClassTfidfTransformer(reduce_frequent_words=True)

vectorizer_model_content = CountVectorizer(stop_words=list(both_stopwords), ngram_range=(2,2))
ctfidf_model_content = ClassTfidfTransformer(reduce_frequent_words=True)

In [4]:
import unicodedata

def normalize_text(text: str) -> str:
    """
    Normalize given text by removing accents.
    
    Args:
        text (str): The input text to be normalized.

    Returns:
        str: The normalized text with accents removed.
    """
    return unicodedata.normalize('NFKD', text).encode('ASCII', 'ignore').decode('utf-8', 'ignore')

In [5]:
cleaned_titles = [normalize_text(title) for title in df['titulo'].values.tolist()]
cleaned_content = [normalize_text(content) for content in df['conteudo'].values.tolist()]

In [6]:
import numpy as np

openai_embeddings_titles_np = np.vstack(df['openai_embedding_title'].values)
openai_embeddings_contents_np = np.vstack(df['openai_embedding_content'].values)

In [7]:
topic_model_title = BERTopic(ctfidf_model=ctfidf_model_title, nr_topics=20, vectorizer_model=vectorizer_model_title)
topics_title, _ = topic_model_title.fit_transform(cleaned_titles, embeddings=openai_embeddings_titles_np)

In [7]:
topic_model_content = BERTopic(ctfidf_model=ctfidf_model_content, nr_topics=20, vectorizer_model=vectorizer_model_content)
topics_content, _ = topic_model_content.fit_transform(cleaned_content, embeddings=openai_embeddings_contents_np)

In [8]:
topic_model_title.get_topic_info()

Topic  Count                                               Name  \
0      -1   1240  -1_talks evento_matricula rpmti_consigo realiz...   
1       0   9873  0_permuta turno_bcc bticc_vaga estagio_turmas bti   
2       1    172  1_camisa 20131_20131 camisa_camisetas 20141_20...   
3       2    150  2_boleiros peladeiros_atencao boleiros_peladei...   
4       3    117  3_institucional dreamspark_dreamspark email_ms...   
5       4    106  4_reforma percurso_proposta reforma_disciplina...   
6       5     41  5_lousas brancas_brancas vidro_substituicao lo...   
7       6     33  6_cade arcondicionado_arcondicionado sala_estu...   
8       7     24  7_cade proficiencia_cade cade_professor cade_p...   
9       8     19                        8_dropbox bti_bti dropbox__   
10      9     17  9_grade grade_upgrade roadsec_grade upgrade_up...   
11     10     17  10_probabilidade inferencia_inferencia nao_equ...   
12     11     17    11_explicacaoinformacao explicacaoinformacao___   
13     12     16  12_expresso imd_imd carona_amiga expresso_caro...   
14     13     15  13_coding championship_ultimate coding_ucc ult...   
15     14     15                                      14_ate ate___   
16     15     14  15_formato documentos_documentos formato_digit...   
17     16     13  16_conversation club_club conversation_open ta...   
18     17     12                                17_kodesh kodesh___   
19     18     11           18_gmtk game_jam 2023_game jam_2023 gmtk   

                                       Representation  \
0   [talks evento, matricula rpmti, consigo realiz...   
1   [permuta turno, bcc bticc, vaga estagio, turma...   
2   [camisa 20131, 20131 camisa, camisetas 20141, ...   
3   [boleiros peladeiros, atencao boleiros, pelade...   
4   [institucional dreamspark, dreamspark email, m...   
5   [reforma percurso, proposta reforma, disciplin...   
6   [lousas brancas, brancas vidro, substituicao l...   
7   [cade arcondicionado, arcondicionado sala, est...   
8   [cade proficiencia, cade cade, professor cade,...   
9          [dropbox bti, bti dropbox, , , , , , , , ]   
10  [grade grade, upgrade roadsec, grade upgrade, ...   
11  [probabilidade inferencia, inferencia nao, equ...   
12  [explicacaoinformacao explicacaoinformacao, , ...   
13  [expresso imd, imd carona, amiga expresso, car...   
14  [coding championship, ultimate coding, ucc ult...   
15                        [ate ate, , , , , , , , , ]   
16  [formato documentos, documentos formato, digit...   
17  [conversation club, club conversation, open ta...   
18                  [kodesh kodesh, , , , , , , , , ]   
19  [gmtk game, jam 2023, game jam, 2023 gmtk, , ,...   

                                  Representative_Docs  
0   [RESPONDA O QUESTIONARIO SOBRE O PERFIL DO EST...  
1   [Levantamento de demandas de turmas para 2019....  
2   [ATLETICA TIRANA - NOVOS PRODUTOS!!!!, ATLETIC...  
3   [ATENCAO "BOLEIROS", "PELADEIROS" ..., ATENCAO...  
4   [MSDN Academic Alliance, MSDN Academic Allianc...  
5   [proposta para a reforma do percurso de discip...  
6   [Substituicao das lousas brancas pelas de vidr...  
7   [AR-CONDICIONADO -LAB III - H4, AR-CONDICIONAD...  
8   [Cade? Cade a proficiencia da boneca?, Cade? C...  
9             [Dropbox BTI, Dropbox BTI, Dropbox BTI]  
10               [Nova grade, Nova grade, Nova grade]  
11  [Probabilidade & Inferencia nao e (mais) equiv...  
12  [Explicacao/Informacao, Explicacao/Informacao,...  
13  [Expresso IMD (Carona Amiga), Expresso IMD (Ca...  
14  [UCC - Ultimate Coding Championship, UCC - Ult...  
15            [Ate quando?, Ate quando?, Ate quando?]  
16  [Formato de Documentos, Formato de Documentos,...  
17  [CONVERSATION CLUB, CONVERSATION CLUB, CONVERS...  
18                           [Kodesh, Kodesh, Kodesh]  
19  [GMTK Game Jam 2023, GMTK Game Jam 2023, GMTK ...

In [8]:
topic_model_content.get_topic_info()

Topic  Count                                               Name  \
0      -1   3592  -1_ate dia_estrutura curricular_matricula extr...   
1       0   5299  0_tecnologia informacao_carga horaria_ciencia ...   
2       1    947                        1_up up_up upp_upp up_ok ok   
3       2    574  2_interesse interesse_tambem interesse_interes...   
4       3    545  3_otima iniciativa_vou querer_camisa bti_helen...   
5       4    333  4_matematicos computacao_fundamentos matematic...   
6       5    131  5_quadros brancos_ficou ruim_vaga carro_quadro...   
7       6    102  6_anexo anexo_anexo edital_arquivo anexo_anexo...   
8       7     92  7_fiz precisa_direitos infelizmente_lucas sao_...   
9       8     85  8_turno original_turno pretendido_20131 noturn...   
10      9     47  9_12981577455 quadra_99294234 988187399_994356...   
11     10     41        10_opcao opcao_opc opcao_opcao opc_opcao kk   
12     11     30  11_respondido respondido_answered respondido_m...   
13     12     26  12_pretendo cursar_cursar pretendo_componente ...   
14     13     17  13_metropole silicio_metropole empresarial_met...   
15     14     15      14_6n1234 7m34_7m34 6n1234_7m34 b116_b116 hmm   
16     15     13                             15_lp1 iden2_lp2 lp1__   
17     16     12                                    16_idem idem___   
18     17     11  17_compartilhar documentos_docx odt_doc docx_s...   
19     18     10  18_notificacao senha_senha alterada_recebi not...   

                                       Representation  \
0   [ate dia, estrutura curricular, matricula extr...   
1   [tecnologia informacao, carga horaria, ciencia...   
2   [up up, up upp, upp up, ok ok, up ok, ok up, a...   
3   [interesse interesse, tambem interesse, intere...   
4   [otima iniciativa, vou querer, camisa bti, hel...   
5   [matematicos computacao, fundamentos matematic...   
6   [quadros brancos, ficou ruim, vaga carro, quad...   
7   [anexo anexo, anexo edital, arquivo anexo, ane...   
8   [fiz precisa, direitos infelizmente, lucas sao...   
9   [turno original, turno pretendido, 20131 notur...   
10  [12981577455 quadra, 99294234 988187399, 99435...   
11  [opcao opcao, opc opcao, opcao opc, opcao kk, ...   
12  [respondido respondido, answered respondido, m...   
13  [pretendo cursar, cursar pretendo, componente ...   
14  [metropole silicio, metropole empresarial, met...   
15  [6n1234 7m34, 7m34 6n1234, 7m34 b116, b116 hmm...   
16               [lp1 iden2, lp2 lp1, , , , , , , , ]   
17                      [idem idem, , , , , , , , , ]   
18  [compartilhar documentos, docx odt, doc docx, ...   
19  [notificacao senha, senha alterada, recebi not...   

                                  Representative_Docs  
0   [O Mes de Seguranca e promovido pela Rede Naci...  
1   [Prezados alunos e demais interessados,\n\nTen...  
2   [Up - Altas Aventuras\n\n, UP! UP! UP!\n, up u...  
3   [Eu tambem tenho interesse.\n, Tambem tenho in...  
4   [Opa galera ! Seguinte, fiz um modelo de camis...  
5   [DIM0404 CALCULO NUMERICO PARA CIENCIA DA COMP...  
6   [Eu faco uso de motocicleta. Ainda nao presenc...  
7   [Informacoes no arquivo em anexo.\n\nFernanda ...  
8   [certo, acompanhando.\n, Sim, Lucas, sao direi...  
9   [Felipe, quero ir pra noite!\n\nNome: Alexandr...  
10  [(84) 988575004 , tudo bem chamar gente de for...  
11  [Opcao 2.\n, opcao 1 e 2 kk\n, Opcao 2, acho q...  
12  [Ja respondi.\n, Respondido. Mas acho que "pux...  
13  [Pretendo cursar\n, Pretendo cursar\n, Pretend...  
14  [OPORTUNIDADE, Voce ja inscreveu sua proposta?...  
15  [B) 6N1234 +7M34\n, B) 6N1234 +7M34\n, B) 6N12...  
16                                    [2\n, 2\n, 2\n]  
17                               [Eu\n, Eu\n, Idem\n]  
18  [Pessoal estive percebendo que algumas pessoas...  
19  [Eu tambem recebi a mesma notificacao de que a...

In [9]:
for idx in range(len(topic_model_title.get_topic_info())):
    print(f'Relevant words - topic {idx}:')
    print(topic_model_title.get_topic(idx))
    print()

Relevant words - topic 0:
[('permuta turno', 0.17327780570374893), ('bcc bticc', 0.1732732257550739), ('vaga estagio', 0.1717186498564334), ('turmas bti', 0.1678296278266885), ('oportunidade estagio', 0.16682935670448726), ('oportunidade bolsa', 0.1626973297436192), ('abaixo assinado', 0.16110683436590736), ('possibilidade turmas', 0.15979816467945782), ('bti sabados', 0.15979816467945782), ('sabados possibilidade', 0.15946106395338983)]

Relevant words - topic 1:
[('camisa 20131', 1.36230715175805), ('20131 camisa', 1.3551349379754447), ('camisetas 20141', 1.3087248539621856), ('20141 camisetas', 1.3003632747879204), ('camisa bti', 1.0730151807088557), ('tirana produtos', 1.0041399284033565), ('produtos atletica', 0.98470238880172), ('bti camisa', 0.98470238880172), ('atletica tirana', 0.9407912380362344), ('camisas bti', 0.894533068857818)]

Relevant words - topic 2:
[('boleiros peladeiros', 1.6303224740870348), ('atencao boleiros', 1.6303224740870348), ('peladeiros atencao', 1.62656

In [9]:
for idx in range(len(topic_model_content.get_topic_info())):
    print(f'Relevant words - topic {idx}:')
    print(topic_model_content.get_topic(idx))
    print()

Relevant words - topic 0:
[('tecnologia informacao', 0.14998042962585748), ('carga horaria', 0.14905309611723627), ('ciencia computacao', 0.13727799935540902), ('engenharia software', 0.13032838101083052), ('processo seletivo', 0.12809012168931114), ('ate dia', 0.12776436574280295), ('secretaria bti', 0.12014345807716564), ('ola pessoal', 0.1166344814061026), ('metropole digital', 0.11639618754056766), ('instituto metropole', 0.11551585713364798)]

Relevant words - topic 1:
[('up up', 2.750521520850081), ('up upp', 0.6220598039496404), ('upp up', 0.5811313290824974), ('ok ok', 0.5678603112340989), ('up ok', 0.5343083152695708), ('ok up', 0.46272457447671317), ('aventuras up', 0.40972832967294626), ('top top', 0.40972832967294626), ('up ac', 0.40972832967294626), ('up altas', 0.40972832967294626)]

Relevant words - topic 2:
[('interesse interesse', 1.5523006389504244), ('tambem interesse', 1.0111477844024017), ('interesse tambem', 0.9604897186356806), ('tambem gostaria', 0.7443176162003

In [11]:
topic_model_title.visualize_barchart(n_words=8, top_n_topics=50, width=500, height=500, title='Topic in titles (OpenAI)')

In [8]:
topic_model_content.visualize_barchart(n_words=8, top_n_topics=50, width=500, height=500, title='Topics by content (OpenAI)')

In [ ]:
wrapped_titles = df['titulo'].str.wrap(90)
wrapped_titles = wrapped_titles.apply(lambda x: x.replace('\n', '<br>'))

fig_clustering_reason = topic_model_title.visualize_documents(topics_title, embeddings=openai_embeddings_titles_np, width=1600, height=900)
fig_clustering_reason.write_html('outputs/clustering_topics_titles.html')
fig_clustering_reason.show()

In [ ]:
wrapped_titles = df['conteudo'].str.wrap(90)
wrapped_titles = wrapped_titles.apply(lambda x: x.replace('\n', '<br>'))

fig_clustering_reason = topic_model_title.visualize_documents(topics_content, embeddings=openai_embeddings_contents_np, width=1600, height=900)
fig_clustering_reason.write_html('outputs/clustering_topics_contents.html')
fig_clustering_reason.show()